<a href="https://colab.research.google.com/github/DrStephPowers/BIA/blob/main/Ch7_RealityMining.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Fitness Tracker Data

In [ ]:
!pip install gpxpy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.6/42.6 kB 1.7 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import pandas as pd

In [ ]:
import gpxpy
import gpxpy.gpx

In [ ]:
def process_gpx_to_df(file_name):
  gpx = gpxpy.parse(open(file_name))

  track = gpx.tracks[0]
  segment = track.segments[0]

  data = []
  segment_length = segment.length_3d()

  for point_idx, point in enumerate(segment.points):
      data.append([point.longitude, point.latitude,point.elevation, point.time, segment.get_speed(point_idx)])
      columns = ["Longitude", "Latitude", "Altitude", "Time", "Speed"]
      gpx_df = pd.DataFrame(data, columns=columns)

  points = []
  for track in gpx.tracks:
      for segment in track.segments:
          for point in segment.points:
              points.append(tuple([point.latitude, point.longitude]))

  return gpx_df, points

In [ ]:
gpx_df, points = process_gpx_to_df('/content/drive/MyDrive/BI BA Handbook/Chapter 7/route_719.gpx')

In [ ]:
gpx_df.head()

Longitude   Latitude     Altitude                      Time     Speed
0 -121.866596  46.938950  1514.531605 2023-07-19 21:28:38+00:00  1.059093
1 -121.866761  46.938657  1513.910954 2023-07-19 21:29:11+00:00  0.919812
2 -121.866766  46.938652  1514.304657 2023-07-19 21:29:12+00:00  0.521158
3 -121.866768  46.938648  1514.534317 2023-07-19 21:29:14+00:00  0.229196
4 -121.866770  46.938647  1514.590483 2023-07-19 21:29:15+00:00  0.154053

In [ ]:
points

[(46.93895, -121.866596),
 (46.938657, -121.866761),
 (46.938652, -121.866766),
 (46.938648, -121.866768),
 (46.938647, -121.86677),
 (46.938648, -121.86677),
 (46.938652, -121.86677),
 (46.938657, -121.866768),
 (46.938662, -121.866767),
 (46.938665, -121.866766),
 (46.938667, -121.866765),
 (46.938669, -121.866765),
 (46.938674, -121.866764),
 (46.93868, -121.866762),
 (46.938684, -121.866761),
 (46.938686, -121.86676),
 (46.938688, -121.86676),
 (46.938691, -121.86676),
 (46.938693, -121.86676),
 (46.938695, -121.86676),
 (46.938697, -121.86676),
 (46.938698, -121.86676),
 (46.938699, -121.866761),
 (46.938701, -121.866762),
 (46.938703, -121.866762),
 (46.938707, -121.866763),
 (46.938711, -121.866764),
 (46.938715, -121.866765),
 (46.93872, -121.866767),
 (46.938723, -121.866769),
 (46.938722, -121.866772),
 (46.938716, -121.866776),
 (46.938708, -121.866781),
 (46.938698, -121.866786),
 (46.938687, -121.866792),
 (46.938677, -121.866798),
 (46.938668, -121.866803),
 (46.938661, -

In [ ]:
import folium

In [ ]:
m = folium.Map(location=(gpx_df["Latitude"].mean(), gpx_df["Longitude"].mean()), tiles="cartodb positron", zoom_start=14)

In [ ]:
for index, row in gpx_df.iterrows():
    marker = folium.CircleMarker(location=(row["Latitude"], row["Longitude"]), radius=1.25)
    marker.add_to(m)

In [ ]:
m

In [ ]:
from matplotlib import cm

In [ ]:
def rgb2hex(rgb):
    rgb = [hex(int(256*x)) for x in rgb]
    r, g, b = [str(x)[2:] for x in rgb]

    return f"#{r}{g}{b}"

In [ ]:
color_mapper = cm.ScalarMappable(cmap=cm.cividis)

In [ ]:
rgb_values = [c[:3] for c in color_mapper.to_rgba(gpx_df["Speed"])]

In [ ]:
colors = [rgb2hex(rgb) for rgb in rgb_values]

In [ ]:
m = folium.Map(location=(gpx_df["Latitude"].mean(), gpx_df["Longitude"].mean()), zoom_start=16, tiles="cartodb positron")

In [ ]:
for point, color, speed in zip(points, colors, gpx_df["Speed"]):
    marker = folium.CircleMarker(location=point,radius=1.25, popup=str(speed), color=color)
    marker.add_to(m)

In [ ]:
m

PRACTICE

In [ ]:
gpx_df, points = process_gpx_to_df('/content/drive/MyDrive/BI BA Handbook/Chapter 7/route_704.gpx')

## Routes

In [ ]:
import numpy as np
import pandas as pd

import requests
import xml.etree.ElementTree as ET
from tqdm import tqdm

import folium

In [ ]:
source = (-113.82483494441753, 52.24678314928733)
dest = (-114.13184057329919, 51.011277826834856)

In [ ]:
start = "{},{}".format(source[0], source[1])
end = "{},{}".format(dest[0], dest[1])

url = 'http://router.project-osrm.org/route/v1/driving/{};{}?alternatives=false&annotations=nodes'.format(start, end)


headers = { 'Content-type': 'application/json'}
r = requests.get(url, headers = headers)
print("Calling API ...:", r.status_code) # Status Code 200 is success


routejson = r.json()
route_nodes = routejson['routes'][0]['legs'][0]['annotation']['nodes']

Calling API ...: 200


In [ ]:
route_list = []
for i in range(0, len(route_nodes)):
    if i % 3==1: #keep every third to speed up algorithm
        route_list.append(route_nodes[i])

coordinates = []

for node in tqdm(route_list):
    try:
        url = 'https://api.openstreetmap.org/api/0.6/node/' + str(node)
        r = requests.get(url, headers = headers)
        myroot = ET.fromstring(r.text)
        for child in myroot:
            lat, long = child.attrib['lat'], child.attrib['lon']
        coordinates.append((lat, long))
    except:
        continue
print(coordinates[:10])

100%|██████████| 309/309 [01:45<00:00,  2.94it/s]

[('52.2472746', '-113.8243749'), ('52.2478143', '-113.8240989'), ('52.2479078', '-113.8245548'), ('52.2480319', '-113.8248660'), ('52.2481590', '-113.8250635'), ('52.2482307', '-113.8251365'), ('52.2485971', '-113.8254927'), ('52.2487515', '-113.8258408'), ('52.2488139', '-113.8262612'), ('52.2488093', '-113.8274170')]


In [ ]:
coordinates[:10]

[('52.2472746', '-113.8243749'),
 ('52.2478143', '-113.8240989'),
 ('52.2479078', '-113.8245548'),
 ('52.2480319', '-113.8248660'),
 ('52.2481590', '-113.8250635'),
 ('52.2482307', '-113.8251365'),
 ('52.2485971', '-113.8254927'),
 ('52.2487515', '-113.8258408'),
 ('52.2488139', '-113.8262612'),
 ('52.2488093', '-113.8274170')]

In [ ]:
m = folium.Map(location=coordinates[0], zoom_start=14, tiles="cartodb positron")

In [ ]:
for point in coordinates:
    marker = folium.CircleMarker(location=point,radius=1.25, color="blue")
    marker.add_to(m)

In [ ]:
m

PRACTICE

Select two locations. Collect their longitude and latitude from Google Maps. Use the code above to plot the route in between.

## Bubble Map

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import pandas as pd
import folium

In [ ]:
trip = pd.read_excel('/content/drive/MyDrive/BI BA Handbook/Chapter 7/reality.xlsx')

In [ ]:
trip.head()

Business        Lat        Long  Visits
0         Costco  52.213176 -113.819368      15
1  Canadian Tire  52.287597 -113.816358      10
2     Michael's   52.240330 -113.817866      10
3     Bower Mall  52.245715 -113.809228       8
4            RDP  52.247334 -113.824985       8

In [ ]:
m = folium.Map(location=(trip["Lat"].mean(), trip["Long"].mean()), tiles="cartodb positron")
m

In [ ]:
m = folium.Map(location=[trip['Lat'].mean(), trip['Long'].mean()], tiles="OpenStreetMap", zoom_start=12)

def get_radius(freq):
    if freq < 2:
        return 2
    elif freq < 5:
        return 5
    elif freq < 10:
        return 10
    else:
        return 15

for i,row in trip.iterrows():
    folium.CircleMarker(
      location=[trip['Lat'].iloc[i], trip['Long'].iloc[i]],
      radius=get_radius(trip["Visits"].iloc[i]),
      color='crimson',
      fill=True,
      fill_color='crimson'
    ).add_to(m)

m